# Projet Webscrapping
---
## Steven LE MOAL Natacha Batmini BATMANABANE

github : https://github.com/Steven-LeMoal/Eco-Product_Recommander (ask invit to : steven.le_moal@edu.devinci.fr, Pr. Mellouli Nedra was invited)

  - [Part 1](#exercise-1) : Installation
  - [Part 2](#exercise-2) : OpenFoodFacts
  - [Part 3](#exercise-3) : Carrefour
  - [Part 4](#exercise-4) : Goût et qualité


<a name="exercise-1">

### Part 1 : Installation
---

In [1]:
#!pip install scrapy

In [2]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException
from selenium.common.exceptions import TimeoutException
import scrapy
from scrapy.crawler import CrawlerProcess
from tqdm import tqdm
import requests
import json
import pandas as pd


Check if the driver is working

In [4]:
driver=webdriver.Chrome('C:/ESILV/S9/Webscrapping/Project/chromedriver.exe') #launch the driver
driver.get('https://www.google.com/') #go to the website 
driver.quit() #quit and close the driver

<ipython-input-4-4a212390be95>:1: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver=webdriver.Chrome('C:/ESILV/S9/Webscrapping/Project/chromedriver.exe') #launch the driver


<a name="exercise-2">

### Part 2 : OpenFoodFacts
---

Install the openfoodfacts package in the current Python environment, which then allows you to use the features offered by this package in the Python notebook.

In [ ]:
#! pip install openfoodfacts

In [6]:
def fetch_carrefour_products_via_requests(page=1):
    """
    Define a function to fetch products from Carrefour using the Open Food Facts API.
    The function takes an optional argument 'page' which defaults to 1.
    """

    url = "https://world.openfoodfacts.org/cgi/search.pl" # URL for the Open Food Facts API.
    # Parameters for the API request.
    params = {
        'search_simple': 1,       # Enables simple search.
        'action': 'process',      # Action to process the search.
        'json': 1,                # Requests the response in JSON format.
        'tagtype_0': 'stores',    # Filters the search by store type.
        'tag_contains_0': 'contains',  # Specifies that the tag should contain the search term.
        'tag_0': 'carrefour',     # Searches for products available in Carrefour stores.
        'page': page,             # Specifies the page number of the search results.
        'page_size': 50           # Sets the number of results per page to 50.
    }

    # Sending a GET request to the API with the specified URL and parameters.
    response = requests.get(url, params=params)

    # Check if the response status code is 200 (OK).
    if response.status_code == 200:
        # If successful, parse and return the JSON data from the response.
        return response.json()
    else:
        # If the request is not successful, return None.
        return None

### Lets do a first scrapping test

In [7]:
carrefour_products = fetch_carrefour_products_via_requests() #get Carrefour products
print(carrefour_products)

{'count': 26662, 'page': 1, 'page_count': 50, 'page_size': 50, 'products': [{'_id': '3274080005003', '_keywords': ['beverage', 'cristaline', 'de', 'eau', 'etat', 'france', 'gurson', 'naturel', 'saint-martin', 'source', 'spring', 'triman', 'water'], 'added_countries_tags': [], 'additives_debug_tags': [], 'additives_n': 0, 'additives_old_n': 0, 'additives_old_tags': [], 'additives_original_tags': [], 'additives_prev_original_tags': [], 'additives_tags': [], 'allergens': '', 'allergens_from_ingredients': '', 'allergens_from_user': '(en) ', 'allergens_hierarchy': [], 'allergens_lc': 'en', 'allergens_tags': [], 'amino_acids_prev_tags': [], 'amino_acids_tags': [], 'brands': 'Cristaline', 'brands_tags': ['cristaline'], 'carbon_footprint_percent_of_known_ingredients': 100, 'categories': 'Beverages,Waters,Spring waters', 'categories_hierarchy': ['en:beverages', 'en:waters', 'en:spring-waters'], 'categories_lc': 'en', 'categories_old': 'Boissons,Eaux,Eaux de sources', 'categories_properties': {'

In [9]:
#example of a line
carrefour_products['products'][10] 

{'_id': '8002270014901',
 '_keywords': ['bergamo',
  'beverage',
  'boissons-sans-sucre-ajoute',
  'carbonated',
  'drink',
  'italia',
  'mineral',
  'natural',
  'pellegrino',
  'san',
  'spring',
  'terme',
  'vegan',
  'vegetarian',
  'water'],
 'abbreviated_product_name': 'S.pellegrino 1l',
 'abbreviated_product_name_fr': 'S.pellegrino 1l',
 'abbreviated_product_name_fr_imported': 'S.pellegrino 1l',
 'added_countries_tags': [],
 'additives_debug_tags': [],
 'additives_n': 0,
 'additives_old_n': 0,
 'additives_old_tags': [],
 'additives_original_tags': [],
 'additives_prev_original_tags': [],
 'additives_tags': [],
 'allergens': '',
 'allergens_from_ingredients': '',
 'allergens_from_user': '(en) ',
 'allergens_hierarchy': [],
 'allergens_lc': 'en',
 'allergens_tags': [],
 'amino_acids_prev_tags': [],
 'amino_acids_tags': [],
 'brands': 'San Pellegrino',
 'brands_imported': 'S. pellegrino',
 'brands_tags': ['san-pellegrino'],
 'categories': 'Beverages, Carbonated drinks, Waters, Sp

In [10]:
# File path where you want to save the JSON data
file_path = 'carrefour_products.json'

# Writing the JSON data to a file
with open(file_path, 'w', encoding='utf-8') as file:
    json.dump(carrefour_products['products'][0], file, ensure_ascii=False, indent=4)

print(f"Data saved to {file_path}")

Data saved to carrefour_products.json


We will keep more column then we will use (here we put all of those that can be useful)

In [11]:
columns_to_keep = [
    "_id",
    "product_name_fr_imported",
    "abbreviated_product_name",
    "abbreviated_product_name_fr",
    "brands_imported",
    "brands_tags",
    "quantity",
    "product_quantity",
    "serving_size",
    "carbon_footprint_percent_of_known_ingredients",
    "categories",
    "categories_tags",
    "code",
    "countries_tags",
    "generic_name",
    "allergens_tags",
    "amino_acids_prev_tags",
    "ecoscore_data",
    "ecoscore_extended_data",
    "ecoscore_grade",
    "ecoscore_score",
    "agribalyse",
    "ingredients_tags",
    "environment_impact_level",
    "environment_impact_level_tags",
    "fruits-vegetables-nuts_100g_estimate"
    "ingredients",
    "ingredients_analysis_tags",
    "nutrient_levels",
    "nutriment"
    "nutriments",
    "nutriments_estimated"
    "nutrition_score_beverage",
    "nutriscore",
    "nutriscore_data",
    "nutriscore_grade",
    "nutriscore_score",
    "vitamins_tags",
    "origins_hierarchy",
    "packaging_hierarchy",
    "packaging",
    "packagings_material_main",
    "product_name",
    "product_name_ro",
    "purchase_tags",
    "stores_tags",
    "url",
    "image_url"
]

In [ ]:
columns_to_keep = [
    "_id",
    "product_name_fr_imported",
    "brands_tags",
    "quantity",
    "ecoscore_score",
    "agribalyse",
    "ingredients_tags",
    "environment_impact_level_tags",
    "ingredients",
    "ingredients_analysis_tags",
    "nutrient_levels",
    "nutriment"
    "nutriments",
    "nutriscore_data",
    "nutriscore_score",
]

### Lets do the full scrapping

In [12]:
def keep_only_col_in_dict(dict_product, cols):
    """
    This function takes a dictionary and a list of columns,
    and returns a new dictionary containing only the key-value pairs
    where the key is in the list of columns.
    """
    new_dict = {}
    # Loop through each column 
    for col in cols:
        # Add the key-value pair to new_dict if the key exists in dict_product; otherwise, add the key with a None value
        new_dict[col] = dict_product.get(col, None)
    return new_dict


def extracted_multiples_page_products(cols, nb_pages=50):
    """
    This function extracts product data from multiple pages,
    processes each product to keep only the specified columns,
    and aggregates them into a single dictionary.
    """
    products_dict = {}
    # Loop through a specified number of pages
    for i in tqdm(range(nb_pages)):
        try:
            # Fetch product data from a specific page
            curr_page =  fetch_carrefour_products_via_requests(page=i)
        except Exception:
            # If there's an exception (like a failed request), print a message and break from the loop
            print(f'Finish early: page {i}/{nb_pages}')
            break
        
        # Get the number of products in the current page
        nb_prod = len(curr_page['products'])
        
        # Loop through each product in the current page
        for j in range(nb_prod):
            # Create a new dictionary for the product containing only the specified columns
            product = keep_only_col_in_dict(curr_page['products'][j], cols)
            # Add the product to the products_dict, using its '_id' as the key
            products_dict[product['_id']] = product
    
    return products_dict


In [13]:
file_path = 'final_extracted_products.json'
extracted_products = extracted_multiples_page_products(
    cols=columns_to_keep,
    nb_pages=200
    )

  0%|          | 0/200 [00:00<?, ?it/s]

100%|██████████| 200/200 [11:59<00:00,  3.60s/it]


In [14]:
df = pd.DataFrame(extracted_products)
openfood = df.transpose()
#openfood.rename(columns={df.columns[0]: 'id'}, inplace=True)


In [15]:
openfood.head(2)

_id product_name_fr_imported  \
3274080005003  3274080005003                     None   
7622210449283  7622210449283                     None   

              abbreviated_product_name abbreviated_product_name_fr  \
3274080005003                     None                        None   
7622210449283                     None                        None   

              brands_imported     brands_tags quantity product_quantity  \
3274080005003            None    [cristaline]    1,5 L             1500   
7622210449283            None  [lu, mondelez]    300 g              300   

              serving_size carbon_footprint_percent_of_known_ingredients  ...  \
3274080005003          1 L                                           100  ...   
7622210449283          20g                                            50  ...   

                                    origins_hierarchy  \
3274080005003  [en:france, fr:Saint-Martin de Gurson]   
7622210449283                                      []   

                                             packaging_hierarchy  \
3274080005003  [en:HdpeFilm-packet, en:aluminium-can, en:ppFi...   
7622210449283  [en:packet, en:Etui en carton, en:Film en plas...   

                                                       packaging  \
3274080005003  HdpeFilm-packet, en:aluminium-can, en:ppFilm-w...   
7622210449283  Packet,Hdpe film-packet,Etui en carton,Film en...   

              packagings_material_main  \
3274080005003                     None   
7622210449283                     None   

                                          product_name product_name_ro  \
3274080005003                            Eau de source      Cristaline   
7622210449283  Prince Chocolat biscuits au blé complet            None   

              purchase_tags  \
3274080005003          None   
7622210449283          None   

                                                     stores_tags  \
3274080005003  [carrefour, leclerc, auchan, intermarche, supe...   
7622210449283  [carrefour-market, magasins-u, auchan, interma...   

                                                             url  \
3274080005003  https://world.openfoodfacts.org/product/327408...   
7622210449283  https://world.openfoodfacts.org/product/762221...   

                                                       image_url  
3274080005003  https://images.openfoodfacts.org/images/produc...  
7622210449283  https://images.openfoodfacts.org/images/produc...  

[2 rows x 45 columns]

In [16]:
openfood.to_csv('DATA/openfood.csv', index=False)

<a name="exercise-2">

### Part 3 : Carrefour
---

In [17]:
openfoodfact = pd.read_csv('DATA/openfood.csv')

In [18]:
openfoodfact.head(2)

_id product_name_fr_imported abbreviated_product_name  \
0  3274080005003                      NaN                      NaN   
1  7622210449283                      NaN                      NaN   

  abbreviated_product_name_fr brands_imported         brands_tags quantity  \
0                         NaN             NaN      ['cristaline']    1,5 L   
1                         NaN             NaN  ['lu', 'mondelez']    300 g   

   product_quantity serving_size  \
0            1500.0          1 L   
1             300.0          20g   

   carbon_footprint_percent_of_known_ingredients  ...  \
0                                          100.0  ...   
1                                           50.0  ...   

                            origins_hierarchy  \
0  ['en:france', 'fr:Saint-Martin de Gurson']   
1                                          []   

                                 packaging_hierarchy  \
0  ['en:HdpeFilm-packet', 'en:aluminium-can', 'en...   
1  ['en:packet', 'en:Etui en carton', 'en:Film en...   

                                           packaging packagings_material_main  \
0  HdpeFilm-packet, en:aluminium-can, en:ppFilm-w...                      NaN   
1  Packet,Hdpe film-packet,Etui en carton,Film en...                      NaN   

                              product_name product_name_ro purchase_tags  \
0                            Eau de source      Cristaline           NaN   
1  Prince Chocolat biscuits au blé complet             NaN           NaN   

                                         stores_tags  \
0  ['carrefour', 'leclerc', 'auchan', 'intermarch...   
1  ['carrefour-market', 'magasins-u', 'auchan', '...   

                                                 url  \
0  https://world.openfoodfacts.org/product/327408...   
1  https://world.openfoodfacts.org/product/762221...   

                                           image_url  
0  https://images.openfoodfacts.org/images/produc...  
1  https://images.openfoodfacts.org/images/produc...  

[2 rows x 45 columns]

In [21]:
openfoodfact.shape

(9950, 45)

In [40]:
driver = webdriver.Chrome() #launch a chrome page
driver.get("https://www.carrefour.fr/s?q=") #go to carrefour search page
wait = WebDriverWait(driver, 7) #wait 7 sec time to go
button = wait.until(EC.element_to_be_clickable((By.ID, "onetrust-reject-all-handler"))) #wait until "accept the cookies" is print
button.click() #click on the "accept the cookies"

In [42]:
def carrefour(codebarre):
    search_bar = driver.find_element(By.XPATH,"/html/body/header/div/div[2]/div[1]/div[3]/div/form/div/div[1]/div/input") #xpath of the sarch bar
    search_bar.send_keys(str(codebarre)) #send the barcode
    search_bar.send_keys(Keys.RETURN) #pressing enter to submit the search
    driver.refresh() #refresh
    try:
        # Tries to find the price of the product by locating the specific element using its XPath.
        # If the element is found, the price is extracted and stored in 'prix'.
        element = driver.find_element(By.XPATH, '/html/body/main/div/div[3]/section/div/div[2]/ul/li[1]/article/div[2]/div[1]/div[2]/div[1]/div/div/div/span[1]')
        prix = element.text
    except NoSuchElementException:
        prix = None

    driver.get("https://www.carrefour.fr/s?q=")  # go back to carrefour search page
    wait = WebDriverWait(driver, 5) #wait 5 sec
    return prix

In [10]:
print(carrefour(openfoodfact['_id'][1]))

refresh
try
3,21


In [84]:
print(carrefour(openfoodfact['_id'][0]))

refresh
none
None


### SCRAPPING

In [61]:
PRICE = pd.DataFrame(columns=['codebarre', 'carrefour', 'gout_qualite'])

In [50]:
PRICE['codebarre'] = openfoodfact['_id'].astype(str)

In [ ]:
for i in range(len(openfoodfact['_id'])):
    PRICE['carrefour'][i] = carrefour(openfoodfact['_id'][i])

In [55]:
driver.quit()

In [58]:
PRICE.head(692)

codebarre carrefour
0    3274080005003      None
1    3017620422003      3,21
2    7622210449283      1,49
3    5449000214911      None
4    3017620425035      5,89
..             ...       ...
687  3083680019408      2,85
688  3161919369286      3,15
689  3179140123805      2,15
690  3245411157944      1,45
691  3302741843104      None

[692 rows x 2 columns]

In [51]:
PRICE_subset = PRICE.head(692)
PRICE_subset.to_csv('PRICE_subset.csv', index=False)

### read

In [62]:
PRICE = pd.read_csv('DATA/PRICE_subset.csv')

In [63]:
PRICE.head(3)

codebarre carrefour
0  3274080005003       NaN
1  3017620422003      3,21
2  7622210449283      1,49

In [54]:
#number of None when i scrapped in Carrefour
PRICE['carrefour'].isnull().sum()

178

In [55]:
692-178

514

<a name="exercise-4">

### Part 4 : Goût et qualité
---

In [57]:
def gout_qualite(codebarre):
    search_bar = driver.find_element(By.XPATH,"/html/body/main/header/div/div/section[1]/div/div/div/div/div/section/div/div/div[2]/div/div/div/div/form/div/input") #xpath of the sarch bar
    search_bar.send_keys(str(codebarre)) #send the barcode
    search_bar.send_keys(Keys.RETURN) #pressing enter to submit the search
    driver.refresh() #refresh
    try:
        # Tries to find the price of the product by locating the specific element using its XPath.
        # If the element is found, the price is extracted and stored in 'prix'.
        element = driver.find_element(By.XPATH, '/html/body/main/section/div/div/section/section/div[3]/div[1]/div/article/div/div[2]/div/div[1]/span[1]')
        prix = element.text
    except NoSuchElementException:
        prix = None

    driver.get("https://goutetqualite.fr/recherche")  # go back to carrefour search page
    #wait = WebDriverWait(driver, 5) #wait 5 sec
    return prix

In [58]:
driver = webdriver.Chrome()
driver.get("https://goutetqualite.fr/recherche")

In [51]:
print(gout_qualite(5449000214911))

1,50 €


In [ ]:
for i in range(len(PRICE['codebarre'])):
    PRICE['gout_qualite'][i] = gout_qualite(PRICE['codebarre'][i])

In [69]:
driver.quit() #fermer le navigateur

In [72]:
PRICE['gout_qualite'] = PRICE['gout_qualite'].str.replace('€', '').str.replace(',', '.').astype(float) #change to a good format

In [75]:
PRICE.head(5)

codebarre carrefour  gout_qualite
0  3274080005003       NaN          0.39
1  3017620422003      3,21          2.95
2  7622210449283      1,49          2.10
3  5449000214911       NaN          1.50
4  3017620425035      5,89         15.95

I want to join product_name from openfoodfact to PRICE

In [77]:
openfoodfact.head(2)

_id product_name_fr_imported abbreviated_product_name  \
0  3274080005003                      NaN                      NaN   
1  7622210449283                      NaN                      NaN   

  abbreviated_product_name_fr brands_imported         brands_tags quantity  \
0                         NaN             NaN      ['cristaline']    1,5 L   
1                         NaN             NaN  ['lu', 'mondelez']    300 g   

   product_quantity serving_size  \
0            1500.0          1 L   
1             300.0          20g   

   carbon_footprint_percent_of_known_ingredients  ...  \
0                                          100.0  ...   
1                                           50.0  ...   

                            origins_hierarchy  \
0  ['en:france', 'fr:Saint-Martin de Gurson']   
1                                          []   

                                 packaging_hierarchy  \
0  ['en:HdpeFilm-packet', 'en:aluminium-can', 'en...   
1  ['en:packet', 'en:Etui en carton', 'en:Film en...   

                                           packaging packagings_material_main  \
0  HdpeFilm-packet, en:aluminium-can, en:ppFilm-w...                      NaN   
1  Packet,Hdpe film-packet,Etui en carton,Film en...                      NaN   

                              product_name product_name_ro purchase_tags  \
0                            Eau de source      Cristaline           NaN   
1  Prince Chocolat biscuits au blé complet             NaN           NaN   

                                         stores_tags  \
0  ['carrefour', 'leclerc', 'auchan', 'intermarch...   
1  ['carrefour-market', 'magasins-u', 'auchan', '...   

                                                 url  \
0  https://world.openfoodfacts.org/product/327408...   
1  https://world.openfoodfacts.org/product/762221...   

                                           image_url  
0  https://images.openfoodfacts.org/images/produc...  
1  https://images.openfoodfacts.org/images/produc...  

[2 rows x 45 columns]

In [79]:
openfoodfact_renamed = openfoodfact.rename(columns={'_id': 'codebarre'})
# Fusionner les deux DataFrames
PRICE= pd.merge(PRICE, openfoodfact_renamed[['codebarre', 'product_name']], on='codebarre', how='left')
PRICE.head()


codebarre carrefour  gout_qualite  \
0  3274080005003       NaN          0.39   
1  3017620422003      3,21          2.95   
2  7622210449283      1,49          2.10   
3  5449000214911       NaN          1.50   
4  3017620425035      5,89         15.95   

                              product_name  
0                            Eau de source  
1                                  Nutella  
2  Prince Chocolat biscuits au blé complet  
3                                Coca-cola  
4                                  Nutella

In [80]:
PRICE.to_csv('DATA/Prices.csv', index=False) #export the df PRICE IN csv